In [29]:
import requests
from PIL import Image
from io import BytesIO
from numpy import asarray
import numpy

r =requests.get('https://api.nasa.gov/planetary/apod?api_key=0eyGPKWmJmE5Z0Ijx25oG56ydbTKWE2H75xuEefx')
result = r.json()
receive = requests.get(result['url'])
img = Image.open(BytesIO(receive.content)).convert('RGB')

with gr.Blocks() as demo:
    with gr.Row():
      with gr.Column():
          gr.Label("Original image")
          input_img = gr.Image(img)
      with gr.Column():
          gr.Label("Image with resolution doubled")
          numpydata = asarray(img)
          output = double_res(numpydata)#numpy.ndarray
          input_img = gr.Image(output)
demo.launch()

1/1 [==============================] - 0s 144ms/step


1/1 [==============================] - 0s 147ms/step
Running on local URL:  http://127.0.0.1:7867

To create a public link, set `share=True` in `launch()`.


(<gradio.routes.App at 0x7f9953260d60>, 'http://127.0.0.1:7867/', None)

In [10]:
import gradio as gr
import numpy as np
from math import ceil
from huggingface_hub import from_pretrained_keras

model = from_pretrained_keras("GIanlucaRub/autoencoder_model_d_0")
def double_res(input_image):
    input_height = input_image.shape[0] 
    input_width = input_image.shape[1] 
    height = ceil(input_height/128)
    width = ceil(input_width/128)
    expanded_input_image = np.zeros((128*height, 128*width,3), dtype=np.uint8)
    np.copyto(expanded_input_image[0:input_height, 0:input_width], input_image)
    
    output_image = np.zeros((128*height*2, 128*width*2,3), dtype=np.float32)

    for i in range(height):
        for j in range(width):
            temp_slice = expanded_input_image[i*128:(i+1)*128, j*128:(j+1)*128]/255
            upsampled_slice = model.predict(temp_slice[np.newaxis, ...]) 
            np.copyto(output_image[i*256:(i+1)*256, j*256:(j+1)*256], upsampled_slice[0])
            if i!= 0 and j!= 0 and i != height-1 and j!=width-1:
# removing inner borders
                right_slice = expanded_input_image[i*128:(i+1)*128, (j+1)*128-64:(j+1)*128+64]/255
                right_upsampled_slice = model.predict(right_slice[np.newaxis, ...]) 
                resized_right_slice = right_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[i*256+64:(i+1)*256-64, (j+1)*256-64:(j+1)*256+64], resized_right_slice)
                
                left_slice = expanded_input_image[i*128:(i+1)*128, j*128-64:(j)*128+64]/255
                left_upsampled_slice = model.predict(left_slice[np.newaxis, ...]) 
                resized_left_slice = left_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[i*256+64:(i+1)*256-64, j*256-64:j*256+64], resized_left_slice)
                
                upper_slice = expanded_input_image[(i+1)*128-64:(i+1)*128+64, j*128:(j+1)*128]/255
                upper_upsampled_slice = model.predict(upper_slice[np.newaxis, ...]) 
                resized_upper_slice = upper_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[(i+1)*256-64:(i+1)*256+64, j*256+64:(j+1)*256-64], resized_upper_slice)
                
                lower_slice = expanded_input_image[i*128-64:i*128+64, j*128:(j+1)*128]/255
                lower_upsampled_slice = model.predict(lower_slice[np.newaxis, ...]) 
                resized_lower_slice = lower_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[i*256-64:i*256+64, j*256+64:(j+1)*256-64], resized_lower_slice)


# removing angles
                lower_right_slice = expanded_input_image[i*128-64:i*128+64, (j+1)*128-64:(j+1)*128+64]/255
                lower_right_upsampled_slice = model.predict(lower_right_slice[np.newaxis, ...]) 
                resized_lower_right_slice = lower_right_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[i*256-64:i*256+64,  (j+1)*256-64:(j+1)*256+64], resized_lower_right_slice)
                
                lower_left_slice = expanded_input_image[i*128-64:i*128+64, j*128-64:j*128+64]/255
                lower_left_upsampled_slice = model.predict(lower_left_slice[np.newaxis, ...]) 
                resized_lower_left_slice = lower_left_upsampled_slice[0][64:192,64:192]
                np.copyto(output_image[i*256-64:i*256+64,  j*256-64:j*256+64], resized_lower_left_slice)
                

                
                
    resized_output_image = output_image[0:input_height*2,0:input_width*2]
    return resized_output_image


2022-12-24 12:18:34.670116: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
config.json not found in /Users/fabio/Downloads/Project/GIanlucaRub/autoencoder_model_d_0
2022-12-24 12:18:40.167772: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


/Users/fabio/opt/anaconda3/lib/python3.9/site-packages/gradio/inputs.py:256: UserWarning: Usage of gradio.inputs is deprecated, and will not be supported in the future, please import your component from gradio.components
  warnings.warn(
/Users/fabio/opt/anaconda3/lib/python3.9/site-packages/gradio/deprecation.py:40: UserWarning: `optional` parameter is deprecated, and it has no effect
  warnings.warn(value)


IMPORTANT: You are using gradio version 3.9.1, however version 3.14.0 is available, please upgrade.
--------
Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


(<gradio.routes.App at 0x7f996ccff940>, 'http://127.0.0.1:7861/', None)